In [1]:
import ibis
from ibis import _
conn = ibis.duckdb.connect(extensions=["spatial"])

In [73]:
state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
county_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-county.parquet"

states = conn.read_parquet(state_boundaries).rename(state_id = "STUSPS", state = "NAME")
county = conn.read_parquet(county_boundaries).rename(county = "NAMELSAD", state = "STATE_NAME")

votes = conn.read_csv("measures.csv")
#votes.execute()
votes.count().execute()

74

In [74]:
#votes.group_by(_.State).agg(n= _.count()).execute()
votes.group_by(_["Jurisdiction Type"]).agg(n= _.count()).execute()
#states.head().execute()

Jurisdiction Type   n
0            County  23
1         Municipal  48
2  Special District   1
3             State   2

In [95]:
vote = (votes
       .filter(_["Jurisdiction Type"] == "County")
       .rename(county = "Jurisdiction Name", state_id = "State")
       .mutate(key = _.county + ibis.literal('-') + _.state_id)
       .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
       .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
       .select('key', 'amount_n', 'amount', 'Status', 'yes')
       )
df = (county
      .join(states.select("state", "state_id"), "state")
      .mutate(key = _.county + ibis.literal('-') + _.state_id)
      .select('key', 'geometry')
      .right_join(vote, "key")
     # .drop('key_right')
     )
# 20 of 23 counties have matches
gdf = df.execute()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [105]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint = {"fill-extrusion-color": outcome, 
         "fill-extrusion-opacity": 0.7,
         "fill-extrusion-height": ["*", ["get", "amount_n"], .001],
        }

#m.add_geojson("vote.geojson")
m.add_gdf(gdf, "fill-extrusion", paint = paint)
m

Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://tiles.openfree…